In [1]:
import csv
import json
import numpy as np
import pandas as pd
import time

from pprint import pprint
csvpath="./input/realestate_data_full.csv"
fileData=[]
data=[]

In [2]:
df = pd.read_csv(csvpath)
df = df.dropna()
df["zipcode"] = df["zipcode"].astype(str)
# del(df["Region"])
df=df.rename(columns={"Month of Period End":"Period", "Median Sale Price":"MSP"})
df.head()

zipcode                           Region  Period     MSP
0   91932  San Diego, CA - Egger Highlands  12-Jan  250000
1   91932  San Diego, CA - Egger Highlands  12-Feb  270000
2   91932  San Diego, CA - Egger Highlands  12-Mar  262000
3   91932  San Diego, CA - Egger Highlands  12-Apr  269000
4   91932  San Diego, CA - Egger Highlands  12-May  262000

In [4]:
hoods=[]
with open('./input/sanDiego_Base.json') as json_file:  
    data = json.load(json_file)

    for d in data['features']:
        hoods.append(d["properties"]["name"])
# print(hoods)

for index, row in df.iterrows():
    for hood in hoods:
        if(row["Region"].find(hood) > -1):
            df.loc[index,"Region"]=hood
        elif(row["Region"].find("Mount Hope") > -1):
            df.loc[index,"Region"]="Mt Hope"
        elif(row["Region"].find("Hollywood Park") > -1):
            df.loc[index,"Region"]="Fairmont Park"
        elif(row["Region"].find("Roseville-Fleet Ridge") > -1):
            df.loc[index,"Region"]="Roseville / Fleet Ridge"
            
            
            
df.head()

zipcode           Region  Period     MSP
0   91932  Egger Highlands  12-Jan  250000
1   91932  Egger Highlands  12-Feb  270000
2   91932  Egger Highlands  12-Mar  262000
3   91932  Egger Highlands  12-Apr  269000
4   91932  Egger Highlands  12-May  262000

In [5]:
# print(hoods)

In [6]:
# for index, row in df.iterrows():
#     if(row["Region"].find("San Diego") == 0):
#         print(row["Region"])

In [7]:
for index, row in df.iterrows():
    x=str(20)+str(row["Period"][0:2])
    y=row["Period"][3:]
    if(y == "Jan" or y == "Feb" or y == "Mar"):
        df.loc[index, "Period"]=(str(x)+"-"+"Q1")
    elif(y == "Apr" or y == "May" or y == "Jun"):
        df.loc[index, "Period"]=(str(x)+"-"+"Q2")
    elif(y == "Jul" or y == "Aug" or y == "Sep"):
        df.loc[index, "Period"]=(str(x)+"-"+"Q3")
    else:
        df.loc[index, "Period"]=(str(x)+"-"+"Q4")
df.head()

zipcode           Region   Period     MSP
0   91932  Egger Highlands  2012-Q1  250000
1   91932  Egger Highlands  2012-Q1  270000
2   91932  Egger Highlands  2012-Q1  262000
3   91932  Egger Highlands  2012-Q2  269000
4   91932  Egger Highlands  2012-Q2  262000

In [8]:
df1=df.groupby(['zipcode', 'Period', 'Region'], as_index=False)['MSP'].mean()
df1.head()

zipcode   Period           Region            MSP
0   91932  2012-Q1  Egger Highlands  260666.666667
1   91932  2012-Q2  Egger Highlands  264333.333333
2   91932  2012-Q3  Egger Highlands  249666.666667
3   91932  2012-Q4  Egger Highlands  271666.666667
4   91932  2013-Q1  Egger Highlands  282333.333333

In [9]:
df1 = df1.round({"MSP":0})

In [10]:
df1.to_csv("cleanedRegionData.csv", index=False)

In [12]:
hoods=[]
with open('./input/sanDiego_Base.json') as json_file:  
    data = json.load(json_file)

    for d in data['features']:
        hood={}
        hood["name"]= d["properties"]["name"]
        hood["geometry"]=d["geometry"]
        hoods.append(hood)
        print(hood["name"])
        time.sleep(.5)
print(hoods)

Qualcomm
Egger Highlands
Old Town
Morena
Midtown
Fairmont Village
Lincoln Park
Grantville
Del Cerro
San Pasqual
Ocean Beach
Mission Bay Park
La Jolla
Torrey Pines
Bay Ho
Linda Vista
Castle
Valencia Park
College East
Clairemont Mesa East
Tierrasanta
Scripps Ranch
Rancho Encantada
Mission Beach
Miramar Ranch North
Mission Bay
North City
Loma Portal
Gaslamp
Hillcrest
North Park
Southcrest
Teralta West
Mt Hope
Teralta East
Ridgeview/Webster
Paradise Hills
Bay Terraces
Sorrento Valley
Serra Mesa
Rancho Bernardo
La Playa
Horton Plaza
Core-Columbia
Burlingame
Stockton
Mountain View
Redwood Village/Rolando Park
Encanto
Mira Mesa
San Carlos
Rancho Penasquitos
Sunset Cliffs
Wooded Area
Pacific Beach
Carmel Valley
Torrey Highlands
South Park
Azalea/Hollywood Park
Chollas View
Colina Del Sol
Ocean Crest
Sherman Heights
Roseville / Fleet Ridge
Normal Heights
Emerald Hills
Mission Hills
Islenair
College West
Allied Gardens
Skyline
Lake Murray
University City
Shelltown
Midway District
Barrio Logan
Ta

In [14]:
f=open("./output/hoodData.json","w+")
# hoodData = json.dumps(hoods)
# print(hoodData)
json.dump(hoods, f)

In [12]:
output={"type":"FeatureCollection"}
features = []

for index, row in df1.iterrows():
    if(row["Region"].find("San Diego") != 0):
        feature={}
        properties={}
        geometry={}

        feature["type"]="Feature"

        properties["time"] = row["Period"]
        properties["region"] = row["Region"]
        properties["med_val"] = row["MSP-Neighborhood"]
        properties["zipcode"] = row["zipcode"]
        feature["properties"]=properties

        for hood in hoods:
            if(hood["name"] == row["Region"]):
                feature["geometry"]=hood["geometry"]

        features.append(feature)
        time.sleep(.25)
# print(features)
output["features"]=features
jsonOutp=[output]
print(json.dumps(jsonOutp))

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=5000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

